In [1]:
import pandas as pd
import numpy as np
import datetime as dt
import altair as alt
from vega_datasets import data

import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, func

from flask import Flask, jsonify

import psycopg2

In [2]:
# Read the CSV file
data = pd.read_csv('Resources/dataset.csv')

# Display the dataprint(data)
data.head(10)

rank  finalWorth               category                 personName   age  \
0     1      211000       Fashion & Retail   Bernard Arnault & family  74.0   
1     2      180000             Automotive                  Elon Musk  51.0   
2     3      114000             Technology                 Jeff Bezos  59.0   
3     4      107000             Technology              Larry Ellison  78.0   
4     5      106000  Finance & Investments             Warren Buffett  92.0   
5     6      104000             Technology                 Bill Gates  67.0   
6     7       94500  Media & Entertainment          Michael Bloomberg  81.0   
7     8       93000                Telecom  Carlos Slim Helu & family  83.0   
8     9       83400            Diversified              Mukesh Ambani  65.0   
9    10       80700             Technology              Steve Ballmer  67.0   

         country         city              source             industries  \
0         France        Paris                LVMH       Fashion & Retail   
1  United States       Austin       Tesla, SpaceX             Automotive   
2  United States       Medina              Amazon             Technology   
3  United States        Lanai              Oracle             Technology   
4  United States        Omaha  Berkshire Hathaway  Finance & Investments   
5  United States       Medina           Microsoft             Technology   
6  United States     New York        Bloomberg LP  Media & Entertainment   
7         Mexico  Mexico City             Telecom                Telecom   
8          India       Mumbai         Diversified            Diversified   
9  United States  Hunts Point           Microsoft             Technology   

  countryOfCitizenship  ... cpi_change_country           gdp_country  \
0               France  ...                1.1   $2,715,518,274,227    
1        United States  ...                7.5  $21,427,700,000,000    
2        United States  ...                7.5  $21,427,700,000,000    
3        United States  ...                7.5  $21,427,700,000,000    
4        United States  ...                7.5  $21,427,700,000,000    
5        United States  ...                7.5  $21,427,700,000,000    
6        United States  ...                7.5  $21,427,700,000,000    
7               Mexico  ...                3.6   $1,258,286,717,125    
8                India  ...                7.7   $2,611,000,000,000    
9        United States  ...                7.5  $21,427,700,000,000    

  gross_tertiary_education_enrollment  \
0                                65.6   
1                                88.2   
2                                88.2   
3                                88.2   
4                                88.2   
5                                88.2   
6                                88.2   
7                                40.2   
8                                28.1   
9                                88.2   

  gross_primary_education_enrollment_country life_expectancy_country  \
0                                      102.5                    82.5   
1                                      101.8                    78.5   
2                                      101.8                    78.5   
3                                      101.8                    78.5   
4                                      101.8                    78.5   
5                                      101.8                    78.5   
6                                      101.8                    78.5   
7                                      105.8                    75.0   
8                                      113.0                    69.4   
9                                      101.8                    78.5   

  tax_revenue_country_country total_tax_rate_country population_country  \
0                        24.2                   60.7       6.705989e+07   
1                         9.6                   36.6       3.282395e+08   
2                         9.6    

In [3]:
# Check for null values
missing_values = data.isnull().sum()
print(missing_values)

rank                                             0
finalWorth                                       0
category                                         0
personName                                       0
age                                             65
country                                         38
city                                            72
source                                           0
industries                                       0
countryOfCitizenship                             0
organization                                  2315
selfMade                                         0
status                                           0
gender                                           0
birthDate                                       76
lastName                                         0
firstName                                        3
title                                         2301
date                                             0
state                          

In [4]:
# Drop unneeded columns
data_dropped = data.drop(columns=['birthMonth', 'birthDay', 'cpi_change_country', 'gross_tertiary_education_enrollment', 'gross_primary_education_enrollment_country', 'life_expectancy_country', 'tax_revenue_country_country', 'total_tax_rate_country', 'organization', 'title', 'residenceStateRegion', 'date', 'state', 'birthYear', 'status'])
data_dropped.head(10)

rank  finalWorth               category                 personName   age  \
0     1      211000       Fashion & Retail   Bernard Arnault & family  74.0   
1     2      180000             Automotive                  Elon Musk  51.0   
2     3      114000             Technology                 Jeff Bezos  59.0   
3     4      107000             Technology              Larry Ellison  78.0   
4     5      106000  Finance & Investments             Warren Buffett  92.0   
5     6      104000             Technology                 Bill Gates  67.0   
6     7       94500  Media & Entertainment          Michael Bloomberg  81.0   
7     8       93000                Telecom  Carlos Slim Helu & family  83.0   
8     9       83400            Diversified              Mukesh Ambani  65.0   
9    10       80700             Technology              Steve Ballmer  67.0   

         country         city              source             industries  \
0         France        Paris                LVMH       Fashion & Retail   
1  United States       Austin       Tesla, SpaceX             Automotive   
2  United States       Medina              Amazon             Technology   
3  United States        Lanai              Oracle             Technology   
4  United States        Omaha  Berkshire Hathaway  Finance & Investments   
5  United States       Medina           Microsoft             Technology   
6  United States     New York        Bloomberg LP  Media & Entertainment   
7         Mexico  Mexico City             Telecom                Telecom   
8          India       Mumbai         Diversified            Diversified   
9  United States  Hunts Point           Microsoft             Technology   

  countryOfCitizenship  selfMade gender        birthDate   lastName firstName  \
0               France     False      M    3/5/1949 0:00    Arnault   Bernard   
1        United States      True      M   6/28/1971 0:00       Musk      Elon   
2        United States      True      M   1/12/1964 0:00      Bezos      Jeff   
3        United States      True      M   8/17/1944 0:00    Ellison     Larry   
4        United States      True      M   8/30/1930 0:00    Buffett    Warren   
5        United States      True      M  10/28/1955 0:00      Gates      Bill   
6        United States      True      M   2/14/1942 0:00  Bloomberg   Michael   
7               Mexico      True      M   1/28/1940 0:00  Slim Helu    Carlos   
8                India     False      M   4/19/1957 0:00     Ambani    Mukesh   
9        United States      True      M   3/24/1956 0:00    Ballmer     Steve   

   cpi_country           gdp_country  population_country  latitude_country  \
0       110.05   $2,715,518,274,227         6.705989e+07         46.227638   
1       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
2       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
3       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
4       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
5       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
6       117.24  $21,427,700,000,000         3.282395e+08         37.090240   
7       141.54   $1,258,286,717,125         1.260140e+08         23.634501   
8       180.44   $2,611,000,000,000         1.366418e+09         20.593684   
9       117.24  $21,427,700,000,000         3.282395e+08         37.090240   

   longitude_country  
0           2.213749  
1         -95.712891  
2         -95.712891  
3         -95.712891  
4         -95.712891  
5         -95.712891  
6         -95.712891  
7        -102.552784  
8          78.962880  
9         -95.712891

In [5]:
# The following line has been run once in order to put the column
# 'finalworth' in billions of dollars instead of millions of dollars.
# Comment it out if you want to run this cell again.

data_dropped['finalWorth'] = data_dropped['finalWorth']/1000

# Rename columns to less clunky titles
# Also restore camel case lost by SQL
data_dropped.rename(columns = {'latitude_country': 'country_lat', 'longitude_country': 'country_long', 'cpi_country': 'country_cpi', 'gdp_country': 'country_gdp', 'population_country': 'country_population'}, inplace = True)
data_dropped.head(10)

rank  finalWorth               category                 personName   age  \
0     1       211.0       Fashion & Retail   Bernard Arnault & family  74.0   
1     2       180.0             Automotive                  Elon Musk  51.0   
2     3       114.0             Technology                 Jeff Bezos  59.0   
3     4       107.0             Technology              Larry Ellison  78.0   
4     5       106.0  Finance & Investments             Warren Buffett  92.0   
5     6       104.0             Technology                 Bill Gates  67.0   
6     7        94.5  Media & Entertainment          Michael Bloomberg  81.0   
7     8        93.0                Telecom  Carlos Slim Helu & family  83.0   
8     9        83.4            Diversified              Mukesh Ambani  65.0   
9    10        80.7             Technology              Steve Ballmer  67.0   

         country         city              source             industries  \
0         France        Paris                LVMH       Fashion & Retail   
1  United States       Austin       Tesla, SpaceX             Automotive   
2  United States       Medina              Amazon             Technology   
3  United States        Lanai              Oracle             Technology   
4  United States        Omaha  Berkshire Hathaway  Finance & Investments   
5  United States       Medina           Microsoft             Technology   
6  United States     New York        Bloomberg LP  Media & Entertainment   
7         Mexico  Mexico City             Telecom                Telecom   
8          India       Mumbai         Diversified            Diversified   
9  United States  Hunts Point           Microsoft             Technology   

  countryOfCitizenship  selfMade gender        birthDate   lastName firstName  \
0               France     False      M    3/5/1949 0:00    Arnault   Bernard   
1        United States      True      M   6/28/1971 0:00       Musk      Elon   
2        United States      True      M   1/12/1964 0:00      Bezos      Jeff   
3        United States      True      M   8/17/1944 0:00    Ellison     Larry   
4        United States      True      M   8/30/1930 0:00    Buffett    Warren   
5        United States      True      M  10/28/1955 0:00      Gates      Bill   
6        United States      True      M   2/14/1942 0:00  Bloomberg   Michael   
7               Mexico      True      M   1/28/1940 0:00  Slim Helu    Carlos   
8                India     False      M   4/19/1957 0:00     Ambani    Mukesh   
9        United States      True      M   3/24/1956 0:00    Ballmer     Steve   

   country_cpi           country_gdp  country_population  country_lat  \
0       110.05   $2,715,518,274,227         6.705989e+07    46.227638   
1       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
2       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
3       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
4       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
5       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
6       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
7       141.54   $1,258,286,717,125         1.260140e+08    23.634501   
8       180.44   $2,611,000,000,000         1.366418e+09    20.593684   
9       117.24  $21,427,700,000,000         3.282395e+08    37.090240   

   country_long  
0      2.213749  
1    -95.712891  
2    -95.712891  
3    -95.712891  
4    -95.712891  
5    -95.712891  
6    -95.712891  
7   -102.552784  
8     78.962880  
9    -95.712891

In [6]:
# Fill in missing values in 'country' column from 'countryOfCitizenship' column
data_dropped['country'] = data_dropped['country'].fillna(data_dropped['countryOfCitizenship'])
missing_values = data_dropped.isnull().sum()
print(missing_values)

rank                      0
finalWorth                0
category                  0
personName                0
age                      65
country                   0
city                     72
source                    0
industries                0
countryOfCitizenship      0
selfMade                  0
gender                    0
birthDate                76
lastName                  0
firstName                 3
country_cpi             184
country_gdp             164
country_population      164
country_lat             164
country_long            164
dtype: int64


In [7]:
# Create a temporary DataFrame with non-null country_lat and country_lng
non_null_lat = data_dropped[data_dropped['country_lat'].notnull()].drop_duplicates(subset='country')[['country', 'country_lat', 'country_long']]

# Now drop the original country_lat and country_lng columns
data_dropped.drop(columns=['country_lat', 'country_long'], inplace=True)

# Merge to find matching countries and fill in the null values
data_dropped = data_dropped.merge(
    non_null_lat,
    on='country',
    how='left'
)

data_dropped.head(10)

rank  finalWorth               category                 personName   age  \
0     1       211.0       Fashion & Retail   Bernard Arnault & family  74.0   
1     2       180.0             Automotive                  Elon Musk  51.0   
2     3       114.0             Technology                 Jeff Bezos  59.0   
3     4       107.0             Technology              Larry Ellison  78.0   
4     5       106.0  Finance & Investments             Warren Buffett  92.0   
5     6       104.0             Technology                 Bill Gates  67.0   
6     7        94.5  Media & Entertainment          Michael Bloomberg  81.0   
7     8        93.0                Telecom  Carlos Slim Helu & family  83.0   
8     9        83.4            Diversified              Mukesh Ambani  65.0   
9    10        80.7             Technology              Steve Ballmer  67.0   

         country         city              source             industries  \
0         France        Paris                LVMH       Fashion & Retail   
1  United States       Austin       Tesla, SpaceX             Automotive   
2  United States       Medina              Amazon             Technology   
3  United States        Lanai              Oracle             Technology   
4  United States        Omaha  Berkshire Hathaway  Finance & Investments   
5  United States       Medina           Microsoft             Technology   
6  United States     New York        Bloomberg LP  Media & Entertainment   
7         Mexico  Mexico City             Telecom                Telecom   
8          India       Mumbai         Diversified            Diversified   
9  United States  Hunts Point           Microsoft             Technology   

  countryOfCitizenship  selfMade gender        birthDate   lastName firstName  \
0               France     False      M    3/5/1949 0:00    Arnault   Bernard   
1        United States      True      M   6/28/1971 0:00       Musk      Elon   
2        United States      True      M   1/12/1964 0:00      Bezos      Jeff   
3        United States      True      M   8/17/1944 0:00    Ellison     Larry   
4        United States      True      M   8/30/1930 0:00    Buffett    Warren   
5        United States      True      M  10/28/1955 0:00      Gates      Bill   
6        United States      True      M   2/14/1942 0:00  Bloomberg   Michael   
7               Mexico      True      M   1/28/1940 0:00  Slim Helu    Carlos   
8                India     False      M   4/19/1957 0:00     Ambani    Mukesh   
9        United States      True      M   3/24/1956 0:00    Ballmer     Steve   

   country_cpi           country_gdp  country_population  country_lat  \
0       110.05   $2,715,518,274,227         6.705989e+07    46.227638   
1       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
2       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
3       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
4       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
5       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
6       117.24  $21,427,700,000,000         3.282395e+08    37.090240   
7       141.54   $1,258,286,717,125         1.260140e+08    23.634501   
8       180.44   $2,611,000,000,000         1.366418e+09    20.593684   
9       117.24  $21,427,700,000,000         3.282395e+08    37.090240   

   country_long  
0      2.213749  
1    -95.712891  
2    -95.712891  
3    -95.712891  
4    -95.712891  
5    -95.712891  
6    -95.712891  
7   -102.552784  
8     78.962880  
9    -95.712891

In [8]:
# Print list of column names for reference in JavaScript
data_dropped.columns

Index(['rank', 'finalWorth', 'category', 'personName', 'age', 'country',
       'city', 'source', 'industries', 'countryOfCitizenship', 'selfMade',
       'gender', 'birthDate', 'lastName', 'firstName', 'country_cpi',
       'country_gdp', 'country_population', 'country_lat', 'country_long'],
      dtype='object')

In [9]:
# Specify the filename
output_filename = 'Resources/data_cleaned.csv'

# Save the DataFrame to a CSV file
data_dropped.to_csv(output_filename, index=False)


In the following cells, we create some initial visualizations from the dataset using the library Altair and the Data package from the library Vega_datasets.

In [10]:
# Connect cleaned data csv as the source
source = 'Resources/data_clean.csv'

NORMALIZEDbarCHART_FW_Ind_selfMade = alt.Chart(source).mark_bar().encode(
    y=alt.Y('sum(finalWorth):Q', stack='normalize'),  # Now 'finalWorth' is treated as quantitative on the y-axis
    x=alt.X('industries:N'),  # 'industries' is now on the x-axis
    color='selfMade:N'  # 'selfMade' remains treated as nominal
).properties(
    title='Normalized Sum of Final Worth by Self-Made Billionaires and Industries'  # Add your title here
)
NORMALIZEDbarCHART_FW_Ind_selfMade

alt.Chart(...)

In [11]:
NORMALIZEDbarCHART_FW_Ind_Gender = alt.Chart(source).mark_bar().encode(
    y=alt.Y('sum(finalWorth):Q', stack='normalize'),  # finalWorth is a quantitative on the y-axis
    x=alt.X('industries:N'),  # industries is on the x-axis
    color=alt.Color('gender:N', scale=alt.Scale(domain=['M', 'F'], range=['blue', 'red']))  # Specify colors for M and F
).properties(
    title='Normalized Sum of Final Worth by Gender and Industries'  # Add your title here
)
NORMALIZEDbarCHART_FW_Ind_Gender

alt.Chart(...)

In [12]:
# Load the cleaned data CSV into a DataFrame
df = pd.read_csv('Resources/data_clean.csv')
# Group by 'Country' and 'Industry', then aggregate the sum of 'FinalWorth' and count of billionaires
aggregated_data = df.groupby(['countryOfCitizenship', 'industries']).agg(
    TotalWorth=('finalWorth', 'sum'),
    BillionaireCount=('finalWorth', 'count')
).reset_index()
# Get the top 10 countries based on the total worth of billionaires
top_countries = aggregated_data.groupby('countryOfCitizenship').agg(
    TotalWorth=('TotalWorth', 'sum'),
    TotalBillionaires=('BillionaireCount', 'sum')
).reset_index()
# Sort and get the top 10 countries
top_countries = top_countries.sort_values(by='TotalWorth', ascending=False).head(10)
# Display the resulting DataFrame
print(top_countries)

   countryOfCitizenship  TotalWorth  TotalBillionaires
73        United States      4490.8                735
13                China      1648.3                491
30                India       674.8                169
22               France       590.0                 43
24              Germany       585.4                126
57               Russia       471.3                104
27            Hong Kong       363.7                 68
11               Canada       245.1                 63
34                Italy       215.6                 64
65          Switzerland       206.3                 41


In [13]:
# Load the cleaned data CSV into a DataFrame
df = pd.read_csv('Resources/data_clean.csv')
# Define the list of countries to filter by
countries_to_filter = [
    'United States', 'China', 'India', 'France',
    'Germany', 'Russia', 'Hong Kong', 'Canada',
    'Italy', 'Switzerland'
]
# Filter the DataFrame based on the 'countryOfCitizenship' column
filtered_df = df[df['countryOfCitizenship'].isin(countries_to_filter)]
# Display the resulting DataFrame
print(filtered_df)

      rank  finalWorth               category                personName   age  \
0        1       211.0       Fashion & Retail  Bernard Arnault & family  74.0   
1        2       180.0             Automotive                 Elon Musk  51.0   
2        3       114.0             Technology                Jeff Bezos  59.0   
3        4       107.0             Technology             Larry Ellison  78.0   
4        5       106.0  Finance & Investments            Warren Buffett  92.0   
...    ...         ...                    ...                       ...   ...   
2634  2540         1.0             Healthcare     Yi Xianzhong & family  63.0   
2635  2540         1.0             Healthcare                   Yu Rong  51.0   
2636  2540         1.0        Food & Beverage    Richard Yuengling, Jr.  80.0   
2637  2540         1.0          Manufacturing             Zhang Gongyun  60.0   
2638  2540         1.0            Real Estate    Zhang Guiping & family  71.0   

            country        

In [14]:
# Used code from Altair's documentation: https://altair-viz.github.io/gallery/stacked_bar_chart_sorted_segments.html
# Used Xpert Learning Assitant to refine code with data types in order to return stacked bar chart
# # Create the stacked bar chart with x-axis sorted alphabetically and altair color scheme
STACKEDbarCHART_finalWorth_countries_industries3 = alt.Chart(filtered_df).mark_bar().encode(
    y='sum(finalWorth):Q',  # Ensure the type is quantitative
    x=alt.X('countryOfCitizenship:N', sort='ascending'),  # Sort alphabetically by countryOfCitizenship
    color=alt.Color('industries:N', scale=alt.Scale(scheme='category20')),  # Use an Altair color scheme
    order=alt.Order(
        'industries:N',  # Specify that industries is nominal
        sort='ascending'
    )
).properties(
    title='Stacked Bar Chart of Final Worth by Country and Industries'
)
STACKEDbarCHART_finalWorth_countries_industries3

alt.Chart(...)

In [15]:
# Used code from Altair's documentation: https://altair-viz.github.io/gallery/normalized_stacked_bar_chart.html
# Used Xpert Learning Assitant to refine code with data types in order to return normalized, stacked bar chart
NORMALIZEDbarCHART_FW_CoC_Ind1 = alt.Chart(filtered_df).mark_bar().encode(
    y=alt.Y('sum(finalWorth):Q', stack='normalize'),  # finalWorth is treated as quantitative on the y-axis
    x=alt.X('countryOfCitizenship:N'),  # countryOfCitizenship is treated as nominal on the x-axis
    color=alt.Color('industries:N', scale=alt.Scale(scheme='category20')),  # Use an Altair color scheme
    order=alt.Order(
        'industries:N',  # Specify that industries is nominal
        sort='ascending'
    )
).properties(
    title='Normalized Final Worth of Billionaires by Country and Industries Stacked Bar Chart'
)
# Display the chart
NORMALIZEDbarCHART_FW_CoC_Ind1

alt.Chart(...)

In [16]:
NORMALIZEDbarCHART_FW_CoC_Gender2 = alt.Chart(filtered_df).mark_bar().encode(
    y=alt.Y('sum(finalWorth):Q', stack='normalize'),
    x=alt.X('countryOfCitizenship:N'),
    color=alt.Color('gender:N', scale=alt.Scale(domain=['M', 'F'], range=['blue', 'red']))  # Specify colors for M and F
).properties(
    title='Normalized Sum of Final Worth by Gender and Country of Citizenship'  # Add your title here
)
NORMALIZEDbarCHART_FW_CoC_Gender2

alt.Chart(...)

In [17]:
NORMALIZEDbarCHART_FW_CoC_SelfMade1 = alt.Chart(filtered_df).mark_bar().encode(
    y=alt.Y('sum(finalWorth):Q', stack='normalize'),  # 'finalWorth' is treated as quantitative on the y-axis
    x=alt.X('countryOfCitizenship:N'),  # 'countryOfCitizenship' is now on the x-axis
    color='selfMade:N'  # 'selfMade' remains treated as nominal
).properties(
    title='Normalized Sum of Final Worth by Self-Made Billionaires and Country of Citizenship'  # Add your title here
)
NORMALIZEDbarCHART_FW_CoC_SelfMade1

alt.Chart(...)